In [80]:
import numpy as np
import pandas as pd

import spice_net as spn

In [81]:
df = pd.read_csv('resources/weather_classification_data.csv')
df = df[(df['Location'] == 'mountain') & (df['Weather Type'] == 'Sunny')]
max_humidity = df['Humidity'].max()
df['cleaned_humidity'] = df['Humidity'].apply(lambda x: x / max_humidity)
max_visibility = df['Visibility (km)'].max()
df['cleaned_visibility'] = df['Visibility (km)'].apply(lambda x: x / max_visibility)
df

Temperature  Humidity  Wind Speed  Precipitation (%)    Cloud Cover  \
2             30.0        64         7.0               16.0          clear   
18            43.0        46         0.5               15.0          clear   
22            33.0        36         7.5               18.0          clear   
28            24.0        61         6.5                3.0  partly cloudy   
41            36.0        22         1.0                0.0          clear   
...            ...       ...         ...                ...            ...   
13146         32.0        59         3.5               13.0          clear   
13154         31.0        55         7.0                7.0  partly cloudy   
13157         33.0        48         1.5                0.0          clear   
13172         33.0        54         0.5               15.0          clear   
13190         30.0        24         3.5               16.0  partly cloudy   

       Atmospheric Pressure  UV Index  Season  Visibility (km)  Location  \
2                   1018.72         5  Spring              5.5  mountain   
18                  1025.80         9  Spring              6.0  mountain   
22                  1014.29         8  Summer              9.5  mountain   
28                  1018.15         7  Autumn              5.5  mountain   
41                  1028.63        10  Summer              5.5  mountain   
...                     ...       ...     ...              ...       ...   
13146               1016.91        11  Autumn              5.5  mountain   
13154               1013.42         9  Winter              6.0  mountain   
13157               1024.96        11  Spring              8.0  mountain   
13172               1012.66         7  Spring              9.0  mountain   
13190               1017.54        11  Summer              6.5  mountain   

      Weather Type  cleaned_humidity  cleaned_visibility  
2            Sunny          0.587156            0.282051  
18           Sunny          0.422018            0.307692  
22           Sunny          0.330275            0.487179  
28           Sunny          0.559633            0.282051  
41           Sunny          0.201835            0.282051  
...            ...               ...                 ...  
13146        Sunny          0.541284            0.282051  
13154        Sunny          0.504587            0.307692  
13157        Sunny          0.440367            0.410256  
13172        Sunny          0.495413            0.461538  
13190        Sunny          0.220183            0.333333  

[1106 rows x 13 columns]

In [82]:
som_size = 50

som_1 = spn.SpiceNetSom(n_neurons=som_size,
                        value_range_start=df['cleaned_humidity'].min(),
                        value_range_end=df['cleaned_humidity'].max(),
                        lrf_tuning_curve=spn.ConstLRF(0.8),
                        lrf_interaction_kernel=spn.ConstLRF(0.8))
som_2 = spn.SpiceNetSom(n_neurons=som_size,
                        value_range_start=df['cleaned_visibility'].min(),
                        value_range_end=df['cleaned_visibility'].max(),
                        lrf_tuning_curve=spn.ConstLRF(0.8),
                        lrf_interaction_kernel=spn.ConstLRF(0.8))

correlation_matrix = spn.SpiceNetHcm(som_1, som_2, spn.ConstLRF(0.8), spn.ConstLRF(0.8))

spice_net = spn.SpiceNet(correlation_matrix)

In [83]:
sub_set = df.sample(n=1000)
train_set = sub_set[:800]
test_set = sub_set[800:]

In [84]:
spice_net.fit(train_set['cleaned_humidity'].tolist(), train_set['cleaned_visibility'].tolist(), 20, 100,
              print_output=True)
spn.plot_som(som_1, True)
spn.plot_som(som_2, True)
spn.plot_hcm(correlation_matrix)

100%|██████████| 8/8 [00:05<00:00,  1.41it/s]


Time spend on the Components: 
Som: 3.463228464126587 s | Convolution Matrix: 2.2030935287475586 s


In [85]:
errors = []
errors_distance = []

for _, row in test_set.iterrows():
    inti_test_value = row['cleaned_humidity']
    result_test_value = row['cleaned_visibility'] * max_visibility
    predicted = spice_net.decode_som_1(inti_test_value) * max_visibility
    errors.append(abs(predicted - result_test_value) / max_visibility * 100)
    errors_distance.append(abs(predicted - result_test_value))
    print(f'Error: {errors[-1]:.6f},\t Predicted: {predicted:.6f},\t Actual: {result_test_value:.6f}')

print('------------------------------------')
print(f'test set length: {len(test_set)}')
print(f'Mean Error in km {np.mean(np.array(errors_distance))}')
print(f'Mean Error in % {np.mean(np.array(errors))}')
print(f'Median Error in % {np.median(np.array(errors))}')

Error: 59.774537,	 Predicted: 19.156035,	 Actual: 7.500000
Error: 0.953952,	 Predicted: 8.186021,	 Actual: 8.000000
Error: 0.064268,	 Predicted: 7.487468,	 Actual: 7.500000
Error: 22.005100,	 Predicted: 5.209005,	 Actual: 9.500000
Error: 9.302458,	 Predicted: 8.186021,	 Actual: 10.000000
Error: 1.421562,	 Predicted: 7.777205,	 Actual: 7.500000
Error: 9.805129,	 Predicted: 6.588000,	 Actual: 8.500000
Error: 0.456945,	 Predicted: 5.910896,	 Actual: 6.000000
Error: 11.748690,	 Predicted: 5.209005,	 Actual: 7.500000
Error: 49.174893,	 Predicted: 5.910896,	 Actual: 15.500000
Error: 13.277457,	 Predicted: 5.910896,	 Actual: 8.500000
Error: 6.653914,	 Predicted: 6.202487,	 Actual: 7.500000
Error: 0.953952,	 Predicted: 8.186021,	 Actual: 8.000000
Error: 10.320679,	 Predicted: 7.487468,	 Actual: 9.500000
Error: 16.876895,	 Predicted: 5.209005,	 Actual: 8.500000
Error: 0.456945,	 Predicted: 5.910896,	 Actual: 6.000000
Error: 6.166598,	 Predicted: 6.202487,	 Actual: 5.000000
Error: 22.005100,	 Pr